In [451]:
import numpy as np
import random
import scipy.stats as stats
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go

- notion of distance (in units)
- notion of space (up, down, right, left) --> arbitrary

1 = move one unit Northeast

-1 = move one unit Southwest

In [489]:
outcome = np.random.binomial(1, 0.5, 10)

direction = {}
direction[0] = 0
cnt = 0
for step in outcome:
    cnt += 1
    if step == 0:
        direction[cnt] = 1
    else:
        direction[cnt] = -1
    
direction_df = pd.DataFrame.from_dict(
    direction, orient='index', columns=['move'])
direction_df.index = direction_df.index.set_names(['step'])

shift = direction_df['move'].shift(periods=1, fill_value=0)
direction_df['running_tally'] = direction_df['move'].cumsum()
direction_df.reset_index(inplace=True)

In [490]:
x_min, x_max = direction_df['running_tally'].min(), \
    direction_df['running_tally'].max()

fig = px.scatter(
        direction_df, 
        x='running_tally', y=np.zeros(len(direction_df)), 
        animation_frame='step',
        range_x=[-4, 4],
        labels={
            'x': 'Distance Traveled',
            'y': 'Northeast - Southwest'
        },
        title='Mosquito Distance Traveled'
        )

fig.update_yaxes(showgrid=False, 
                zeroline=True, zerolinecolor='grey', zerolinewidth=1,
                showticklabels=False)

### Locally Euclidean

Binomial likelihood:
 - mosquito can fly North, East, South, or West; aka up or down and left or right.
 - $p = 0.5$ means that for any given day, the mosquito is equally likely to choose one of the four options from above.
 - we assume each _unit step_ is 1km

Steps in the direction of North and East are **positive** vales on a 2d x-y plane

Steps in the direction of South and West are **negative** values on 2d x-y plane

In [625]:
def plot_2d_walk(df):

    fig = go.Figure(
    layout=go.Layout(
        xaxis=dict(range=[-50, 50], autorange=False),
        yaxis=dict(range=[-50, 50], autorange=False),
        width=1000, height=650,
        xaxis_title='Units (East or West)',
        yaxis_title='Units (North or South)',
        title="Mosquito Random Walk (2d)",
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None])])]
        )
    )

    fig.add_trace(
        go.Scatter(
            x=df.x[:1],
            y=df.y[:1]
        )
    )

    fig.update(frames=[
        go.Frame(data=[go.Scatter(x=df.x[:k], y=df.y[:k])])
            for k in range(1, len(df) + 1)
        ]
    )

    fig.show()

In [630]:
def mosquito_random_walk_2d(n_steps):

    x_steps = np.random.choice([-1, 1], n_steps)
    y_steps = np.random.choice([-1, 1], n_steps)
    x_pos, y_pos = np.cumsum(x_steps), np.cumsum(y_steps)


    df = pd.DataFrame({
        'step': np.arange(0, n_steps),
        'x': x_pos,
        'y': y_pos
    })

    plot_2d_walk(df)


In [632]:
mosquito_random_walk_2d(n_steps=500)